# Group assignment Pandas - dataset SYKE

For this part of the assignment we decided to utilise the open data provided by the Finnish Environment Institute (SYKE), section Hydrology on their website https://www.syke.fi/en-US/Open_information/Open_web_services/Environmental_data_API.

For downloading and saving the data in the CSV format we used https://pragmatiqa.com/xodata/# to be able to download the data in batches up to 50000 lines as the SYKE's API doesn't allow automatically to download batches bigger than 500 lines.

Our goal will be combining SYKE's datasets on the ice thickness and water temperature in Finnish lakes over the history when these have been measured and analyse the changes over this time frame. We retrieved various simple datasets from the SYKE's database which will be merged together to get more comprehensive data for further analysis. Since each dataset is dependent on the temperature developments in the past we'd expect a strong correlation across all data from these datasets.

<img src="https://drive.google.com/uc?export=download&id=1TDvTLatcpcrsKhrjSpiVVKBRMc-RQne8" height=1200 width=750 alt="Pond hockey on Saimaa lake in Mikkeli (2018)">

                          Pond hockey on frozen Saimaa lake in Mikkeli (©Teemu Paappanen, 2018)

In [1]:
import pandas as pd
import numpy as np
# import matplotlib.pyplot as plt
import plotly.express as px
from plotly.offline import iplot, init_notebook_mode
import cufflinks as cf

%matplotlib inline
init_notebook_mode(connected=True)
cf.go_offline(connected=True)
cf.set_config_file(theme="pearl")

## Combining data of ice thickness

All files are saved as csv so we used the Pandas read_csv() function to load them into Jupyter notebook.

In [2]:
ice_thickness1 = pd.read_csv("./SYKE_source_files/Ice_thickness_1_4.csv", sep=",")
ice_thickness2 = pd.read_csv("./SYKE_source_files/Ice_thickness_2_4.csv", sep=",")
ice_thickness3 = pd.read_csv("./SYKE_source_files/Ice_thickness_3_4.csv", sep=",")
ice_thickness4 = pd.read_csv("./SYKE_source_files/Ice_thickness_4_4.csv", sep=",")

During the download process from the SYKE's API the dates at the end of each but last files were cut in the middle and then started from the beginning in the following file. This fact is visible when presenting the last and first couple of rows of the files below and will have to be addressed when merging the files together.

In [3]:
print(ice_thickness1.tail(2), "\n")
print(ice_thickness2.head(2), "\n")
print(ice_thickness2.tail(2), "\n")
print(ice_thickness3.head(2), "\n")
print(ice_thickness3.tail(2), "\n")
print(ice_thickness4.head(2), "\n")
print(ice_thickness4.tail(2))

       Paikka_Id                 Aika  Arvo  Lippu_Id
49998        495  1987-03-20T00:00:00    22        37
49999        496  1987-03-20T00:00:00    21        37 

   Paikka_Id                 Aika  Arvo  Lippu_Id
0        401  1987-03-20T00:00:00    17        37
1        402  1987-03-20T00:00:00    18        37 

       Paikka_Id                 Aika  Arvo  Lippu_Id
49998        413  2000-02-28T00:00:00    52        41
49999        421  2000-02-28T00:00:00    39        41 

   Paikka_Id                 Aika  Arvo  Lippu_Id
0        402  2000-02-28T00:00:00     0        37
1        409  2000-02-28T00:00:00    19        37 

       Paikka_Id                 Aika  Arvo  Lippu_Id
49998        495  2016-11-20T00:00:00     0        37
49999        503  2016-11-20T00:00:00     0        37 

   Paikka_Id                 Aika  Arvo  Lippu_Id
0        449  2016-11-20T00:00:00     0        37
1        470  2016-11-20T00:00:00     0        37 

       Paikka_Id                 Aika  Arvo  Lippu_I

We'll merge all 4 files together to create a single DataFrame and also rename the columns by their English translations.

In [4]:
ice_thickness_orig = pd.concat([ice_thickness1,ice_thickness2,ice_thickness3,ice_thickness4], ignore_index=True)
ice_thickness = ice_thickness_orig.copy()
ice_thickness.columns = ["Place_Id", "Date", "Value", "Flag_Id"]

In [5]:
ice_thickness.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 164868 entries, 0 to 164867
Data columns (total 4 columns):
 #   Column    Non-Null Count   Dtype 
---  ------    --------------   ----- 
 0   Place_Id  164868 non-null  int64 
 1   Date      164868 non-null  object
 2   Value     164868 non-null  int64 
 3   Flag_Id   164868 non-null  int64 
dtypes: int64(3), object(1)
memory usage: 5.0+ MB


As we can see in the DataFrame overview above, the **Date** column's Dtype is *object* so we'll change it to Pandas' *datetime* to be able to work with it better during our analysis. At the same time we create a column called **Place_date** by combining the **Place_Id** and **Date** columns and then remove any duplicates.

In [6]:
ice_thickness["Date"] = pd.to_datetime(ice_thickness["Date"])
ice_thickness["Place_date"] = ice_thickness.Place_Id.astype(str).str.cat(ice_thickness.Date.astype(str), sep="_")

In [7]:
ice_thickness.drop_duplicates(inplace=True)

At last we'll check whether there's any missing data and if so remove such rows from the DataFrame.

In [8]:
ice_thickness.isna().sum()

Place_Id      0
Date          0
Value         0
Flag_Id       0
Place_date    0
dtype: int64

## Combining data of water temperatures

Again all files are saved as csv so we used the Pandas read_csv() function to load them into Jupyter notebook. However, since there's 10 files in total this time we'll use a for-loop to simplify the DataFrame creation process.

In [9]:
water_temperature = pd.read_csv("./SYKE_source_files/Surface_Water_Temperature_1_10.csv", sep=",")
for i in range(2,11):
    water_file = pd.read_csv(f"./SYKE_source_files/Surface_Water_Temperature_{i}_10.csv", sep=",")
    water_temperature = pd.concat([water_temperature, water_file], ignore_index=True)

In [10]:
water_temperature.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 473104 entries, 0 to 473103
Data columns (total 3 columns):
 #   Column     Non-Null Count   Dtype  
---  ------     --------------   -----  
 0   Paikka_Id  473104 non-null  int64  
 1   Aika       473104 non-null  object 
 2   Arvo       473104 non-null  float64
dtypes: float64(1), int64(1), object(1)
memory usage: 10.8+ MB


As in the ice thickness DataFrame also in this case we'll change the **Date** column Dtype to *datetime*, create a new column called **Place_date** by combining the **Place_Id** and **Date** columns and then remove any duplicates.

In [11]:
water_temperature.columns = ["Place_Id", "Date", "Value"]
water_temperature["Date"] = pd.to_datetime(water_temperature["Date"])
water_temperature["Place_date"] = water_temperature.Place_Id.astype(str).str.cat(water_temperature.Date.astype(str), sep="_")

In [12]:
water_temperature.drop_duplicates(inplace=True)
water_temperature.reset_index(inplace=True, drop=True)

Again we'll check whether there's any missing data and if so remove such rows.

In [13]:
water_temperature.isna().sum()

Place_Id      0
Date          0
Value         0
Place_date    0
dtype: int64

## Brief overview of both datasets

In [14]:
ice_thickness.describe(include="all", datetime_is_numeric=True)

Place_Id                           Date          Value  \
count   164748.000000                         164748  164748.000000   
unique            NaN                            NaN            NaN   
top               NaN                            NaN            NaN   
freq              NaN                            NaN            NaN   
mean       652.294425  1994-12-06 22:58:06.983789696      27.487593   
min        401.000000            1910-01-15 00:00:00       0.000000   
25%        440.000000            1985-03-20 00:00:00      10.000000   
50%        479.000000            1995-01-30 00:00:00      24.000000   
75%        521.000000            2008-05-10 00:00:00      43.000000   
max       3809.000000            2020-11-25 00:00:00     126.000000   
std        647.676468                            NaN      20.939959   

              Flag_Id      Place_date  
count   164748.000000          164748  
unique            NaN           51857  
top               NaN  500_2018-04-02  
freq              NaN               7  
mean        43.028456             NaN  
min         37.000000             NaN  
25%         38.000000             NaN  
50%         40.000000             NaN  
75%         41.000000             NaN  
max        114.000000             NaN  
std         16.494750             NaN

In [15]:
water_temperature.describe(include="all", datetime_is_numeric=True)

Place_Id                           Date          Value  \
count   472962.000000                         472962  472962.000000   
unique            NaN                            NaN            NaN   
top               NaN                            NaN            NaN   
freq              NaN                            NaN            NaN   
mean      1795.825096  1984-06-12 08:01:03.024093312      10.261295   
min       1657.000000            1916-04-30 00:00:00       0.000000   
25%       1670.000000            1970-09-01 00:00:00       3.800000   
50%       1685.000000            1983-01-17 00:00:00      10.900000   
75%       1707.000000            2002-07-02 00:00:00      16.200000   
max       3485.000000            2020-11-26 00:00:00      28.800000   
std        326.195987                            NaN       6.787038   

                      Place_date  
count                     472962  
unique                    472962  
top     1716_2013-10-07 00:00:00  
freq                           1  
mean                         NaN  
min                          NaN  
25%                          NaN  
50%                          NaN  
75%                          NaN  
max                          NaN  
std                          NaN

From the overviews above we realised we didn't get all unique values in the **ice_thickness** DataFrame's column **Place_date** as expected. The reason needs to be investigated and fixed as we expected only one observation per location per day.

In [16]:
ice_thickness["Flag_Id"].value_counts()

41     51657
37     34141
38     32185
40     23718
39     14270
112     2920
114     2857
113     2824
43       176
Name: Flag_Id, dtype: int64

In [17]:
flag_ids = list(ice_thickness["Flag_Id"].unique())
print(flag_ids)

[41, 37, 38, 40, 39, 112, 113, 114, 43]


Based on the observations above we concluded that the reason for duplicate **Place_date** values is several **Flag_Id**s assigned to some of the daily observations. Therefore we need to import also another SYKE dataset in JSON format to understand better what these **Flag_Id**s refer to and whether we could drop some of the observations.

In [18]:
lippu_file = pd.read_json("./SYKE_source_files/Lippu.json")

In [19]:
lippu = pd.json_normalize(data=lippu_file["value"])

In [20]:
lippu[lippu["Lippu_id"].isin(flag_ids)]

Lippu_id        LippuKoodi  \
35        37      Lumen syvyys   
36        38       Veden pinta   
37        39        Kohvasauva   
38        40  Kohva+Vesikerros   
39        41       Jäänpaksuus   
41        43        Heikko jää   
57       112             Kohva   
58       113          Teräsjää   
59       114        Vesikerros   

                                               Kuvaus KuvausEng  
35             Lumen syvyys kairausreiän päältä (cm)       None  
36  Veden korkeus jään alareunasta veden pintaan (cm)      None  
37  Sauvasta luetun lumen tai lumettoman jään kork...      None  
38  Kairausreiästä mitatun kohvan paksuus (cm) + J...      None  
39   Jään kokonaispaksuus alareunasta yläreunaan (cm)      None  
41  Jäätä on näköpiirissä, mutta se on liian heikk...      None  
57         Kairausreiästä mitatun kohvan paksuus (cm)      None  
58      Kairausreiästä mitatun teräsjään paksuus (cm)      None  
59  Jään välissä olevien mahdollisten vesikerroste...      None

We imported and normalised the JSON data, then filtered only **Flag_Id**s found in our **ice_thickness** dataset to simplify the investigation. Based on the analysis above we can confirm that the only **Flag_Id** value relevant for our analysis is no. 41 as that one indicates the ice thickness in cm. The remaining flags aren't important for our analysis and therefore we'll remove them from the DataFrame. At the same time we'll rename the **Value** column to **Ice_thickness_cm** to clarify its values' meaning.

In [21]:
ice_thickness.rename(columns={"Value":"Ice_thickness_cm"}, inplace=True)

In [22]:
ice_thickness = ice_thickness[ice_thickness["Flag_Id"] == 41]

In [23]:
ice_thickness.describe(include="all", datetime_is_numeric=True)

Place_Id                           Date  Ice_thickness_cm  \
count   51657.000000                          51657      51657.000000   
unique           NaN                            NaN               NaN   
top              NaN                            NaN               NaN   
freq             NaN                            NaN               NaN   
mean      595.791258  1987-03-15 21:15:13.432843712         41.462841   
min       401.000000            1910-01-15 00:00:00          0.000000   
25%       438.000000            1974-03-15 00:00:00         29.000000   
50%       473.000000            1988-02-10 00:00:00         42.000000   
75%       516.000000            2002-04-10 00:00:00         54.000000   
max      3809.000000            2020-11-21 00:00:00        126.000000   
std       547.415068                            NaN         18.256687   

        Flag_Id      Place_date  
count   51657.0           51657  
unique      NaN           51657  
top         NaN  474_1980-01-30  
freq        NaN               1  
mean       41.0             NaN  
min        41.0             NaN  
25%        41.0             NaN  
50%        41.0             NaN  
75%        41.0             NaN  
max        41.0             NaN  
std         0.0             NaN

Now we can see that all **Place_date** values are unique and all **Flag_Id** values are equal to 41 as intended. The **Flag_Id** column doesn't bring us any extra information anymore so we can drop it out of the Datarame and at the same time we can also reset the index.

In [24]:
ice_thickness.drop(columns=["Flag_Id"], inplace=True)
ice_thickness.reset_index(inplace=True, drop=True)

Now we seem to be having both datasets ready for deeper analysis.

In [25]:
ice_thickness_new = ice_thickness.set_index("Date")

## Historical development of measuring locations (Place_Ids)

In [26]:
place_ids_annual_count = ice_thickness_new.resample("A").nunique()["Place_Id"]

In [38]:
place_ids_annual_count.iplot(kind="bar", y="Place_Id", color="blue")

## Historical avg. ice thickness in Finland

In [28]:
ice_thickness_annual_avg = ice_thickness_new.resample("A").mean()["Ice_thickness_cm"]
historical_mean = ice_thickness_new["Ice_thickness_cm"].mean()

In [29]:
ice_thickness_annual_avg.iplot(kind="bar", y="Ice_thickness_cm", yTitle="cm", color="blue",
                               hline=dict(y=historical_mean, color="coral",dash="dash",width=2))

## Ice thickness history of the Place_Id with the most observations

In [30]:
print(ice_thickness_new["Place_Id"].value_counts().head())
top_Place_Id = 402 # Saimaa lake in Lappeenranta

402    1245
450    1135
444    1069
531    1052
470     999
Name: Place_Id, dtype: int64


In [49]:
most_active_Place_Id = ice_thickness_new[ice_thickness_new["Place_Id"] == top_Place_Id]
most_active_Place_Id_annual = most_active_Place_Id.resample("A").agg({"Ice_thickness_cm":[np.mean, np.min, np.max]})
most_active_Place_Id_annual.iplot(mode="lines",
                                  y=[("Ice_thickness_cm","mean"),
                                     ("Ice_thickness_cm", "amin"),
                                     ("Ice_thickness_cm", "amax")],
                                  width=2,
                                  bestfit=True,
                                 interpolation="spline")

## Untidy dataset

Next we can see how it'd look like if we re-arranged the data and do the basic tidying but we wouldn't work with annual values, i.e. we'd get observations on monthly (or even more frequent) basis.

In [33]:
ice_full = pd.pivot_table(ice_thickness, index="Date",
                          values=["Ice_thickness_cm", "Place_Id"],
                          aggfunc={"Ice_thickness_cm":np.mean, "Place_Id":pd.Series.nunique})
ice_full.iplot(kind="bar", y="Ice_thickness_cm", secondary_y="Place_Id")

The visualisation becomes quite really messy and the only understanding from this chart can be that the amount of **Place_Id**s increased.

In [34]:
ice_thickness.iplot(kind="bar", y="Place_Id", color="blue")

In [35]:
ice_thickness_new.iplot(kind="bar", y="Place_Id", color="blue")

In [36]:
ice_thickness_new.iplot(kind="bar", y="Ice_thickness_cm", yTitle="cm", color="blue",
                               hline=dict(y=historical_mean, color="coral",dash="dash",width=2))

## Conclusion

As proven by the visualiation despite of the dataset being relatively clean it was necessary to do further adjustments for us to be able to visualise the data meaningfully and get clear understanding.

Based on the brief data analysis we found out there was a significant increase in locations at which ice thickness levels are being measured during the 60's. This fact would need further investigation to see whether this was caused by expanded amount of stations, missing data from the past or some other reason.

Due to the same fact the average ice levels for the whole country can't be taken as a relevant information for our analysis since the difference in the amount of locations before and after this change surely impacted the measured ice levels.

We selected the lake with the highest amount of observations for a deeper analysis. This location was lake Saimaa in the city of Lappeenranta with obserations done continuously since 1917. We calculated and visualised minimum, maximum and average annual ice levels in this location to get better understanding on the ice thickness level development thru the history. We can conclude that there has been a decrease in all parameters, the main impact being on the maximum levels.